# Daten Extraktion aus dem Bundesanzeiger

## Vorbereitung

In [77]:
import pandas as pd

from aki_prj23_transparenzregister.utils.data_extraction.bundesanzeiger import (
    Bundesanzeiger,
)

ba_wrapper = Bundesanzeiger()
# df_reports = ba_wrapper.get_information("Törmer Energy Solar 1 GmbH & Co. KG", "")
# df_reports = ba_wrapper.get_information("Atos IT-Dienstleistung und Beratung GmbH", "")
df_reports = ba_wrapper.get_information(
    "Stadtwerke Haltern am See Gesellschaft mit beschränkter Haftung", ""
)
df_reports.head()

date                                            company  \
1 2022-10-21  Stadtwerke Haltern am See Gesellschaft mit bes...   
3 2021-10-12  Stadtwerke Haltern am See Gesellschaft mit bes...   
5 2020-12-03  Stadtwerke Haltern am See Gesellschaft mit bes...   
6 2020-01-09  Stadtwerke Haltern am See Gesellschaft mit bes...   
7 2019-10-10  Stadtwerke Haltern am See Gesellschaft mit bes...   

                                          raw_report  jahr  \
1  <div class="publication_container">\n <div cla...  2021   
3  <div class="publication_container">\n <div cla...  2020   
5  <div class="publication_container">\n <div cla...  2019   
6  <div class="publication_container">\n <div cla...  2018   
7  <div class="publication_container">\n <div cla...  2017   

                                            auditors  \
1  [Auditor(name='Volker Voelcker', company='Pric...   
3  [Auditor(name='Hubert Ahlers', company='Pricew...   
5  [Auditor(name='Hubert Ahlers', company='Pricew...   
6  [Auditor(name='Hubert Ahlers', company='Pricew...   
7                                                 []   

                                   financial_results  
1  {'revenue': 46275.0, 'net_income': 1757.0, 'eb...  
3  {'revenue': 47459.0, 'net_income': 1661.0, 'eb...  
5  {'revenue': 45575.0, 'net_income': 1599.0, 'eb...  
6  {'revenue': 43898.0, 'net_income': 2043.0, 'eb...  
7                                                 {}

## Daten Extraktion

In [78]:
from bs4 import BeautifulSoup
from io import StringIO

In [79]:
sample_report = df_reports.iloc[1].raw_report

### Aufsichtsrat

**TODO**

### Bilanz bzw. GuV

In [80]:
def parse_tables(report: str) -> list:
    result = []
    soup = BeautifulSoup(report, features="html.parser")
    for table in soup.find_all("table", {"class": "std_table"}):
        df = pd.read_html(StringIO(str(table)), flavor="bs4")[0]
        print(df.columns)
        print(df.dtypes)
        result.append(df)
    return result


tables = parse_tables(sample_report)

MultiIndex([('Unnamed: 0_level_0', 'Unnamed: 0_level_1'),
            (              '2020',                 'T€'),
            (              '2019',                 'T€'),
            (       'Veränderung',                 'T€'),
            (       'Veränderung',                  '%')],
           )
Unnamed: 0_level_0  Unnamed: 0_level_1     object
2020                T€                    float64
2019                T€                    float64
Veränderung         T€                      int64
                    %                       int64
dtype: object
MultiIndex([('Unnamed: 0_level_0', 'Unnamed: 0_level_1'),
            (              '2020',                 'T€'),
            (              '2020',                  '%'),
            (              '2019',                 'T€'),
            (              '2019',                  '%'),
            (     'Veränderungen',                 'T€'),
            (     'Veränderungen',                  '%')],
           )
Unnamed: 0_l

In [81]:
current_table = tables[1]
current_table.head()

Unnamed: 0_level_0     2020           2019       Veränderungen  \
              Unnamed: 0_level_1       T€     %       T€     %            T€   
0                   Umsatzerlöse   47.459   978   45.575   970         1.884   
1     Aktivierte Eigenleistungen  380.000     8  400.000     9       -20.000   
2  Sonstige betriebliche Erträge  687.000    14  991.000    21      -304.000   
3           Betriebliche Erträge   48.526  1000   46.966  1000         1.560   
4                Materialaufwand   34.007   701   32.647   695         1.360   

        
     %  
0   41  
1  -50  
2 -307  
3   33  
4   42

In [82]:
import re


def cleanse_string(value: str) -> str:
    if value is not None and isinstance(value, str):
        return re.sub(r"(.+\.).", "", value)
    return None

In [83]:
for index, row in current_table.iterrows():
    current_table.iloc[index][0] = cleanse_string(row[0])
current_table.head()

C:\Users\trist\AppData\Local\Temp\ipykernel_15672\152097142.py:2: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  current_table.iloc[index][0] = cleanse_string(row[0])
C:\Users\trist\AppData\Local\Temp\ipykernel_15672\152097142.py:2: FutureWarning: Series.__setitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To set a value by position, use `ser.iloc[pos] = value`
  current_table.iloc[index][0] = cleanse_string(row[0])


Unnamed: 0_level_0     2020           2019       Veränderungen  \
              Unnamed: 0_level_1       T€     %       T€     %            T€   
0                   Umsatzerlöse   47.459   978   45.575   970         1.884   
1     Aktivierte Eigenleistungen  380.000     8  400.000     9       -20.000   
2  Sonstige betriebliche Erträge  687.000    14  991.000    21      -304.000   
3           Betriebliche Erträge   48.526  1000   46.966  1000         1.560   
4                Materialaufwand   34.007   701   32.647   695         1.360   

        
     %  
0   41  
1  -50  
2 -307  
3   33  
4   42

In [84]:
def parse_string_to_float(value) -> float:
    try:
        if value is None:
            return None
        if isinstance(value, float):
            return value
        return float(value.replace(".", "").replace(",", "."))
    except Exception as e:
        return None


def apply_factor(value, factor: float):
    transformed_value = parse_string_to_float(value)
    if transformed_value is None or isinstance(transformed_value, str):
        return None
    result = transformed_value * factor
    # print(result)
    return result

In [85]:
converter = {
    "Mio€": 1 * 10**6,
    "Mio": 1 * 10**6,
    "T€": 1 * 10**3,
    "TEUR": 1 * 10**3,
    "EUR": 1,
    "€": 1,
}

for column in current_table.columns:
    if isinstance(column, tuple):
        for c in column:
            for x, factor in converter.items():
                if x in c:
                    current_table[column] = current_table[column].apply(
                        lambda x: apply_factor(x, factor)
                    )
                    next
    else:
        for x, factor in converter.items():
            parts = column.split(" ")
            for y in parts:
                if re.match(x, y):
                    current_table[column] = current_table[column].apply(
                        lambda x: apply_factor(x, factor)
                    )
                    current_table.rename({column: parts[0]}, inplace=True, axis=1)
                    next
                # print(current_table[column])
current_table.dropna(axis=0, how="all", inplace=True)
current_table.dropna(axis=1, how="all", inplace=True)
current_table.head()

Unnamed: 0_level_0      2020            2019        \
              Unnamed: 0_level_1        T€     %        T€     %   
0                   Umsatzerlöse   47459.0   978   45575.0   970   
1     Aktivierte Eigenleistungen  380000.0     8  400000.0     9   
2  Sonstige betriebliche Erträge  687000.0    14  991000.0    21   
3           Betriebliche Erträge   48526.0  1000   46966.0  1000   
4                Materialaufwand   34007.0   701   32647.0   695   

  Veränderungen       
             T€    %  
0        1884.0   41  
1      -20000.0  -50  
2     -304000.0 -307  
3        1560.0   33  
4        1360.0   42

In [86]:
current_table.dtypes

Unnamed: 0_level_0  Unnamed: 0_level_1     object
2020                T€                    float64
                    %                       int64
2019                T€                    float64
                    %                       int64
Veränderungen       T€                    float64
                    %                       int64
dtype: object

In [87]:
# Remove columns hosting non-numerics; excl. first column hosting keys
columns_to_prune = []
for column_index, column_type in enumerate(current_table.dtypes[1:]):
    if column_type in ["object", "str"]:
        columns_to_prune.append(column_index + 1)

current_table = current_table.drop(
    current_table.columns[columns_to_prune], axis="columns"
)

In [88]:
# Prune rows where first columns is None
import numpy as np

current_table = current_table.replace(to_replace="None", value=np.nan).dropna()
current_table

Unnamed: 0_level_0      2020            2019        \
                           Unnamed: 0_level_1        T€     %        T€     %   
0                                Umsatzerlöse   47459.0   978   45575.0   970   
1                  Aktivierte Eigenleistungen  380000.0     8  400000.0     9   
2               Sonstige betriebliche Erträge  687000.0    14  991000.0    21   
3                        Betriebliche Erträge   48526.0  1000   46966.0  1000   
4                             Materialaufwand   34007.0   701   32647.0   695   
5                             Personalaufwand    6258.0   129    6222.0   132   
6                              Abschreibungen    2239.0    46    2273.0    48   
7                           Konzessionsabgabe    1331.0    27    1302.0    28   
8   Übrige sonstige betriebliche Aufwendungen    2100.0    43    2066.0    44   
9                   Betriebliche Aufwendungen   45935.0   947   44510.0   948   
10       Ergebnis der betrieblichen Tätigkeit    2591.0    53    2456.0    52   
11     Finanzergebnis (Ertrags-/Aufwandsaldo)  -13000.0     0  -99000.0    -2   
12                           sonstige Steuern  147000.0     3  164000.0     3   
13                          Neutraler Bereich  134000.0     3   65000.0     1   
14         Jahresüberschuss vor Ertragsteuern    2457.0    51    2391.0    51   
15                              Ertragsteuern  796000.0    16  792000.0    17   
16                           Jahresüberschuss    1661.0    34    1599.0    34   

   Veränderungen        
              T€     %  
0         1884.0    41  
1       -20000.0   -50  
2      -304000.0  -307  
3         1560.0    33  
4         1360.0    42  
5        36000.0     6  
6       -34000.0   -15  
7        29000.0    22  
8        34000.0    16  
9         1425.0    32  
10      135000.0    55  
11       86000.0  -869  
12      -17000.0  -104  
13       86000.0  1062  
14       66000.0    28  
15        4000.0     5  
16       62000.0    39

In [89]:
kpis = {}
for _index, row in current_table.iterrows():
    kpis[row[0]] = row[1]
kpis

C:\Users\trist\AppData\Local\Temp\ipykernel_15672\340569398.py:3: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  kpis[row[0]] = row[1]


{'Umsatzerlöse': 47459.0,
 'Aktivierte Eigenleistungen': 380000.0,
 'Sonstige betriebliche Erträge': 687000.0,
 'Betriebliche Erträge': 48526.0,
 'Materialaufwand': 34007.0,
 'Personalaufwand': 6258.0,
 'Abschreibungen': 2239.0,
 'Konzessionsabgabe': 1331.0,
 'Übrige sonstige betriebliche Aufwendungen': 2100.0,
 'Betriebliche Aufwendungen': 45935.0,
 'Ergebnis der betrieblichen Tätigkeit': 2591.0,
 'Finanzergebnis (Ertrags-/Aufwandsaldo)': -13000.0,
 'sonstige Steuern': 147000.0,
 'Neutraler Bereich': 134000.0,
 'Jahresüberschuss vor Ertragsteuern': 2457.0,
 'Ertragsteuern': 796000.0,
 'Jahresüberschuss': 1661.0}

In [90]:
import re


def get_bilanz(report: str) -> any:
    result = {}
    soup = BeautifulSoup(report, features="html.parser")
    for pos in ["Aktiva", "Passiva"]:
        tag = soup.find("b", string=re.compile(pos))
        if tag:
            pos_results = pd.read_html(
                StringIO(str(tag.findNext("table", {"class": "std_table"})))
            )[0]
            result[pos] = pos_results
        else:
            result[pos] = pd.DataFrame([])
    return result

In [91]:
bilanz = get_bilanz(sample_report)
bilanz["Passiva"].head()

Investitionen (netto)  2020  T€  2019  T€  Veränderung  T€
0       Stromversorgung     1.372     1.553         -181.000
1         Gasversorgung   713.000   707.000            6.000
2  sonstige Aktivitäten   661.000     2.605           -1.944
3             Insgesamt     2.746     4.865           -2.119

In [92]:
bilanz["Aktiva"].head()

Unnamed: 0_level_0 31. Dezember 2020        31. Dezember 2019         \
  Unnamed: 0_level_1                T€      %                T€      %   
0     Anlagevermögen               NaN    NaN               NaN    NaN   
1        Sachanlagen            28.919  689.0            28.812  689.0   
2      Finanzanlagen             2.667   64.0             4.189  100.0   
3                NaN            31.586  753.0            33.001  789.0   
4     Umlaufvermögen               NaN    NaN               NaN    NaN   

  Veränderung  
           T€  
0         NaN  
1     107.000  
2      -1.522  
3      -1.415  
4         NaN

In [93]:
from IPython.display import display, HTML

# Assuming that dataframes df1 and df2 are already defined:
display(HTML(bilanz["Passiva"].to_html()))

In [94]:
def get_tables(raw_report: str) -> list:
    soup = BeautifulSoup(raw_report, features="html.parser")
    tables = soup.find_all("table", {"class": "std_table"})
    dfs = []
    for table in tables:
        for df in pd.read_html(StringIO(str(table))):
            dfs.append(df)
    return dfs


for df in get_tables(sample_report):
    print(df.columns)

tables = get_tables(sample_report)

MultiIndex([('Unnamed: 0_level_0', 'Unnamed: 0_level_1'),
            (              '2020',                 'T€'),
            (              '2019',                 'T€'),
            (       'Veränderung',                 'T€'),
            (       'Veränderung',                  '%')],
           )
MultiIndex([('Unnamed: 0_level_0', 'Unnamed: 0_level_1'),
            (              '2020',                 'T€'),
            (              '2020',                  '%'),
            (              '2019',                 'T€'),
            (              '2019',                  '%'),
            (     'Veränderungen',                 'T€'),
            (     'Veränderungen',                  '%')],
           )
MultiIndex([('Unnamed: 0_level_0', 'gerundet'),
            (              '2020',       'T€'),
            (              '2019',       'T€'),
            (       'Veränderung',       'T€'),
            (       'Veränderung',        '%')],
           )
MultiIndex([('Unnamed: